In [71]:

%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import azureml.core
from azureml.core import Workspace , Dataset


Azure ML SDK Version:  1.2.0


In [74]:
dataset= pd.read_csv("tw.csv", names=["Col1","Col2","Col3","Col4","Col5","Col6"], encoding='ISO-8859-1') 
#data preprocessing- done
from nltk.tokenize import TweetTokenizer
tknzr = TweetTokenizer(strip_handles=True, reduce_len=True)
from nltk.stem import WordNetLemmatizer 
from nltk.stem import PorterStemmer 
import string
import re

# Init the Wordnet Lemmatizer
lemmatizer = WordNetLemmatizer()
#ps = PorterStemmer()
#dataset['Col6']=dataset['Col6'].apply(lambda x: " ".join(ps.stem(i) for i in tknzr.tokenize(x) ))
dataset['Col6']=dataset['Col6'].apply(lambda x: " ".join(lemmatizer.lemmatize(i) for i in tknzr.tokenize(x) ))
####
dataset['Col6']=dataset['Col6'].apply(lambda x: re.sub("@S+|www?:\S+|https?:\S+|http?:\S|[^A-Za-z0-9]+",' ',x))
dataset= dataset.dropna(axis=0, how="any")

dataset['Col6']=dataset['Col6'].str.replace('\d+', '').apply(lambda x:str(x).translate(str.maketrans('', '', string.punctuation)).lower().rstrip())
dataset['Col6']

0            awww that s a bummer you shoulda got david c...
1          is upset that he can t update his facebook by ...
2          i dived many time for the ball managed to save...
3               my whole body feel itchy and like it on fire
4          no it s not behaving at all i m mad why am i h...
5                                         not the whole crew
6                                                 need a hug
7          hey long time no see yes rains a bit only a bi...
8                                   nope they didn t have it
9                                               que me muera
10                   spring break in plain city it s snowing
11                                  i just re pierced my ear
12         i couldn t bear to watch it and i thought the ...
13         it it count idk why i did either you never tal...
14         i would ve been the first but i didn t have a ...
15         i wish i got to watch it with you i miss you a...
16         hollis death 

In [75]:
dataset= dataset[["Col1","Col6"]]
dataset= dataset.dropna(axis=0,how="any")
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize 
stop_words = set(stopwords.words('english')) 
dataset

Col1                                               Col6
0           0    awww that s a bummer you shoulda got david c...
1           0  is upset that he can t update his facebook by ...
2           0  i dived many time for the ball managed to save...
3           0       my whole body feel itchy and like it on fire
4           0  no it s not behaving at all i m mad why am i h...
5           0                                 not the whole crew
6           0                                         need a hug
7           0  hey long time no see yes rains a bit only a bi...
8           0                           nope they didn t have it
9           0                                       que me muera
10          0            spring break in plain city it s snowing
11          0                           i just re pierced my ear
12          0  i couldn t bear to watch it and i thought the ...
13          0  it it count idk why i did either you never tal...
14          0  i would ve been the first but i didn t have a ...
15          0  i wish i got to watch it with you i miss you a...
16          0  hollis death scene will hurt me severely to wa...
17          0                                  about to file tax
18          0  ahh ive always wanted to see rent love the sou...
19          0  oh dear were you drinking out of the forgotten...
20          0   i wa out most of the day so didn t get much done
21          0  one of my friend called me and asked to meet w...
22          0                   i baked you a cake but i ated it
23          0               this week is not going a i had hoped
24          0                           blagh class at  tomorrow
25          0      i hate when i have to call and wake people up
26          0  just going to cry myself to sleep after watchi...
27          0                              im sad now miss lilly
28          0  oooh lol that leslie and ok i won t do it agai...
29          0  meh almost lover is the exception this track g...
...       ...                                                ...
1599970     4   thanks thanks that wa just what i wa looking for
1599971     4  thanks martin not the most imaginative interfa...
1599972     4                            congrats mike way to go
1599973     4                  omg office space i wanna steal it
1599974     4  ahaha nooo you were just away from everyone el...
1599975     4  hey i m baack and thanks so much for all those...
1599976     4     yeah my conscience would be clear in that case
1599977     4               thats my girl dishing out the advice
1599978     4                                      i second that
1599979     4                                      in the garden
1599980     4       jo jen by nemuselo zrovna t holce ael co nic
1599981     4                     another commenting contest yay
1599982     4  i figured out how to see my tweet and facebook...
1599983     4  theri tomorrow drinking coffee talking about o...
1599984     4  you heard it here first we re having a girl ho...
1599985     4  if ur the lead singer in a band beware falling...
1599986     4                             too much ad on my blog
1599987     4  neveer i think that you both will get on well ...
1599988     4  ha good job that s right we gotta throw that b...
1599989     4                              im glad ur doing well
1599990     4                                  wooo xbox is back
1599991     4  mmmm that sound absolutely perfect but my sche...
1599992     4                   recovering from the long weekend
1599993     4                                                   
1599994     4  yeah that doe work better than just waiting fo...
1599995     4  just woke up having no school is the best feel...
1599996     4    thewdb com very cool to hear old walt interview
1599997     4  are you ready for your mojo makeover ask me fo...
1599998     4  happy th birthday to my boo of alll time tupac...
1599999     4                               

In [76]:
dataset['Col6'] = dataset['Col6'].apply(lambda x: [w for w in word_tokenize(x) if not w in stop_words])
dataset['Col6']

0          [awww, bummer, shoulda, got, david, carr, thir...
1          [upset, update, facebook, texting, might, cry,...
2          [dived, many, time, ball, managed, save, rest,...
3                     [whole, body, feel, itchy, like, fire]
4                                       [behaving, mad, see]
5                                              [whole, crew]
6                                                [need, hug]
7          [hey, long, time, see, yes, rains, bit, bit, l...
8                                                     [nope]
9                                               [que, muera]
10                     [spring, break, plain, city, snowing]
11                                            [pierced, ear]
12         [bear, watch, thought, ua, loss, wa, embarrass...
13                [count, idk, either, never, talk, anymore]
14         [would, first, gun, really, though, zac, snyde...
15                    [wish, got, watch, miss, wa, premiere]
16         [hollis, deat

# Simple model

Word vectors has been averaged into 1D corpus representation

In [77]:
ds=dataset
from gensim.models import Word2Vec
# define training data
word_tokens=ds['Col6']
# train model size!
model = Word2Vec(word_tokens, min_count=1, size=8,workers=cpu_count())
# summarize vocabulary
words = list(model.wv.vocab)
print(words)


['awww', 'bummer', 'shoulda', 'got', 'david', 'carr', 'third', 'day', 'upset', 'update', 'facebook', 'texting', 'might', 'cry', 'result', 'school', 'today', 'also', 'blah', 'dived', 'many', 'time', 'ball', 'managed', 'save', 'rest', 'go', 'bound', 'whole', 'body', 'feel', 'itchy', 'like', 'fire', 'behaving', 'mad', 'see', 'crew', 'need', 'hug', 'hey', 'long', 'yes', 'rains', 'bit', 'lol', 'fine', 'thanks', 'nope', 'que', 'muera', 'spring', 'break', 'plain', 'city', 'snowing', 'pierced', 'ear', 'bear', 'watch', 'thought', 'ua', 'loss', 'wa', 'embarrassing', 'count', 'idk', 'either', 'never', 'talk', 'anymore', 'would', 'first', 'gun', 'really', 'though', 'zac', 'snyder', 'doucheclown', 'wish', 'miss', 'premiere', 'hollis', 'death', 'scene', 'hurt', 'severely', 'film', 'wry', 'director', 'cut', 'file', 'tax', 'ahh', 'ive', 'always', 'wanted', 'rent', 'love', 'soundtrack', 'oh', 'dear', 'drinking', 'forgotten', 'table', 'drink', 'get', 'much', 'done', 'one', 'friend', 'called', 'asked', '

In [78]:
dic={}
ww=list(model.wv.vocab)
for i in ww:
    dic.update({i:model.wv[i].mean()})


In [79]:
final=[]
for i in ds["Col6"]:
    arr=[]
    for u in i:
        if u in dic.keys():
            arr.append(dic[u])
        else:
            print("problem")
    final.append(arr)

In [80]:
#keeping 20 words per tweet

for i in final:
    if len(i)<21:
        for b in range(len(i),20):
            i.append(0)
    elif len(i)>20:
        b=len(i)
        while b>20:
            i.pop(b-1)
            b=b-1

In [81]:
#check nr tweets
max=0
min=90
for i in final:
    if len(i)>max:
        max=len(i)
    if len(i)<min:
        min=len(i)
print(min)
print(max)

20
20


In [82]:
X= pd.DataFrame(final)
X.shape

(1600000, 20)

In [83]:
ds['Col1']= ds['Col1'].replace(4,1)
Y=ds['Col1']
Y.shape


(1600000,)

In [84]:
%time
# Import `Sequential` from `keras.models`
from keras.models import Sequential
from sklearn.model_selection import train_test_split
# Import `Dense` from `keras.layers`
from keras.layers import Dense
from keras.layers import SimpleRNN

# Initialize the constructor
model = Sequential()



# Add an input layer 
model.add(Dense(20, activation='relu', input_shape=(20,)))
model.add(Dense(16, activation='relu'))

model.add(Dense(12, activation='relu'))
# Add one hidden layer 
model.add(Dense(8, activation='relu'))




# Add an output layer 
model.add(Dense(1, activation='sigmoid'))
model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])


X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=42)


model.fit(X_train, y_train,epochs= 10, batch_size=5, verbose=1, validation_split=0.2 )


Wall time: 0 ns
Train on 1024000 samples, validate on 256000 samples
Epoch 1/10
1024000/1024000 [==============================] - 249s 243us/step - loss: 0.6722 - accuracy: 0.5678 - val_loss: 0.6709 - val_accuracy: 0.5682
Epoch 2/10
1024000/1024000 [==============================] - 246s 240us/step - loss: 0.6703 - accuracy: 0.5699 - val_loss: 0.6710 - val_accuracy: 0.5692
Epoch 3/10
1024000/1024000 [==============================] - 236s 230us/step - loss: 0.6696 - accuracy: 0.5704 - val_loss: 0.6700 - val_accuracy: 0.5702
Epoch 4/10
1024000/1024000 [==============================] - 201s 196us/step - loss: 0.6694 - accuracy: 0.5705 - val_loss: 0.6700 - val_accuracy: 0.5697
Epoch 5/10
1024000/1024000 [==============================] - 184s 180us/step - loss: 0.6691 - accuracy: 0.5706 - val_loss: 0.6698 - val_accuracy: 0.5697
Epoch 6/10
1024000/1024000 [==============================] - 194s 190us/step - loss: 0.6687 - accuracy: 0.5716 - val_loss: 0.6705 - val_accuracy: 0.5710
Epoch 7

In [85]:
loss,acc= model.evaluate(X_test,y_test)
print(acc)

320000/320000 [==============================] - 3s 9us/step
0.5732812285423279


In [86]:
y_scores = model.predict_classes(X_test)
from sklearn.metrics import roc_auc_score
roc_auc_score(y_test, y_scores)


0.5731775798474544

# Multiple dimentions
Keeping vectors and loading them into Embeding layer of keras model

In [87]:
dataset= pd.read_csv("tw.csv", names=["Col1","Col2","Col3","Col4","Col5","Col6"], encoding='ISO-8859-1') 
#data preprocessing- done
from nltk.tokenize import TweetTokenizer
tknzr = TweetTokenizer(strip_handles=True, reduce_len=True)
from nltk.stem import WordNetLemmatizer 
from nltk.stem import PorterStemmer 
import string
import re
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize 
from multiprocessing import cpu_count
stop_words = set(stopwords.words('english')) 

# Init the Wordnet Lemmatizer
#lemmatizer = WordNetLemmatizer()
ps = PorterStemmer()
dataset['Col6']=dataset['Col6'].apply(lambda x: " ".join(ps.stem(i) for i in tknzr.tokenize(x) if not i in stop_words ))
#dataset['Col6']=dataset['Col6'].apply(lambda x: " ".join(lemmatizer.lemmatize(i) for i in tknzr.tokenize(x) if not i in stop_words ))
####
#dataset['Col6'] = dataset['Col6'].apply(lambda x: [w for w in word_tokenize(x) if not w in stop_words])
dataset['Col6']=dataset['Col6'].apply(lambda x: re.sub("@S+|www?:\S+|https?:\S+|http?:\S|[^A-Za-z0-9]+",' ',x))

dataset['Col1']= dataset['Col1'].replace(4,1)
dataset['Col6']=dataset['Col6'].str.replace('\d+', '').apply(lambda x:str(x).translate(str.maketrans('', '', string.punctuation)).lower().rstrip())
dataset= dataset[["Col1","Col6"]]
dataset= dataset.dropna(axis=0,how="any")
ds= dataset

In [88]:
from multiprocessing import cpu_count

from gensim.models import FastText, Word2Vec
# define training data
tokenized= ds
word_tokens= tokenized['Col6'].apply(lambda x: [w for w in word_tokenize(x)])#if not w in stop_words
nrDimentsions=100
model = Word2Vec(word_tokens, min_count=1, size=nrDimentsions,workers=cpu_count())
#model.train(word_tokens,total_examples=len(word_tokens),epochs=10)
# summarize vocabulary
words = list(model.wv.vocab)
print(words)

# save the vectors in a new matrix
embedding_matrix = np.zeros((len(model.wv.vocab) + 1, nrDimentsions))
for i, vec in enumerate(model.wv.vectors):
    embedding_matrix[i] = vec

['awww', 'that', 'bummer', 'you', 'shoulda', 'got', 'david', 'carr', 'third', 'day', 'd', 'upset', 'can', 't', 'updat', 'facebook', 'text', 'might', 'cri', 'result', 'school', 'today', 'also', 'blah', 'i', 'dive', 'mani', 'time', 'ball', 'manag', 'save', 'the', 'rest', 'go', 'bound', 'whole', 'bodi', 'feel', 'itchi', 'like', 'fire', 'behav', 'm', 'mad', 'see', 'crew', 'need', 'hug', 'hey', 'long', 'ye', 'rain', 'bit', 'lol', 'fine', 'thank', 'how', 'nope', 'que', 'muera', 'spring', 'break', 'plain', 'citi', 'snow', 're', 'pierc', 'ear', 'bear', 'watch', 'and', 'thought', 'ua', 'loss', 'embarrass', 'it', 'count', 'idk', 'either', 'never', 'talk', 'anymor', 'would', 'v', 'first', 'gun', 'realli', 'though', 'zac', 'snyder', 'doucheclown', 'wish', 'miss', 'premier', 'holli', 'death', 'scene', 'hurt', 'sever', 'film', 'wri', 'director', 'cut', 'file', 'tax', 'ahh', 'ive', 'alway', 'want', 'rent', 'love', 'soundtrack', 'oh', 'dear', 'were', 'drink', 'forgotten', 'tabl', 'get', 'much', 'done'

In [89]:
model.train(word_tokens,total_examples=len(word_tokens),epochs=10)

WARNING - Effective 'alpha' higher than previous training cycles


(114008008, 128642950)

In [104]:
# more imports
from sklearn.model_selection import train_test_split
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

# how many features should the tokenizer extract
features = embedding_matrix.shape[0]
tokenizer = Tokenizer(num_words = features)
# fit the tokenizer on our text
tokenizer.fit_on_texts(ds['Col6'])

# get all words that the tokenizer knows
word_index = tokenizer.word_index

# put the tokens in a matrix
X = tokenizer.texts_to_sequences(ds['Col6'])
X = pad_sequences(X)

# prepare the labels
y = pd.get_dummies(ds['Col1'])

# split in train and test
X_train, X_test, y_train, y_test = train_test_split(X, ds['Col1'], test_size=0.1, random_state=42)

In [105]:
import pickle

# saving tokenizer to file
with open('tokenizer.pkl', 'wb') as handle:
    pickle.dump(tokenizer, handle, protocol=pickle.HIGHEST_PROTOCOL)


In [106]:
X.shape

(1600000, 42)

In [108]:
from keras.models import Sequential
from keras.layers import LSTM, Dense, Embedding, Dropout, Activation,Conv1D,MaxPooling1D

# init model
mod = Sequential()
# emmbed word vectors
mod.add(Embedding(len(model.wv.vocab)+1,nrDimentsions,input_length=X.shape[1],weights=[embedding_matrix],trainable=False))
mod.add(Dropout(0.25))

#mod.add(MaxPooling1D(pool_size=4))
mod.add(LSTM(200))
#200 twice longer 0.77%

mod.add(Dense(1))
mod.add(Activation('sigmoid'))


mod.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

In [109]:
%time
from keras.callbacks import ReduceLROnPlateau, EarlyStopping
mod.fit(X_train,y_train,epochs= 2, batch_size=5, verbose=1, validation_split=0.2, callbacks= [ ReduceLROnPlateau(monitor='val_loss', patience=5, cooldown=0),
              EarlyStopping(monitor='val_acc', min_delta=1e-4, patience=5)])

Wall time: 0 ns
Train on 1152000 samples, validate on 288000 samples
Epoch 1/2
1152000/1152000 [==============================] - 6624s 6ms/step - loss: 0.5190 - accuracy: 0.7387 - val_loss: 0.4913 - val_accuracy: 0.7598
Epoch 2/2
      5/1152000 [..............................] - ETA: 10:35:46 - loss: 0.4988 - accuracy: 0.6000

C:\Users\lesh3\Anaconda3\lib\site-packages\keras\callbacks\callbacks.py:846: RuntimeWarning: Early stopping conditioned on metric `val_acc` which is not available. Available metrics are: val_loss,val_accuracy,loss,accuracy,lr
  (self.monitor, ','.join(list(logs.keys()))), RuntimeWarning


1152000/1152000 [==============================] - 5783s 5ms/step - loss: 0.5062 - accuracy: 0.7485 - val_loss: 0.4892 - val_accuracy: 0.7605


In [110]:
acc= mod.evaluate(X_test,y_test)
print(acc)

y_scores = mod.predict_classes(X_test)


160000/160000 [==============================] - 52s 327us/step
[0.4875005011588335, 0.7616750001907349]


In [111]:
#saving keras model to file
model_json = mod.to_json()
with open("model.json", "w+") as json_file:
    json_file.write(model_json)
mod.save_weights("model.h5")

In [112]:
roc_auc_score(y_test, y_scores)

0.7615551844385061